<a href="https://colab.research.google.com/github/Samir-atra/BDSD_Minor_Project/blob/main/MediaPipe_Stuff.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
# Download and install packages
# !python -m pip install mediapipe
# !wget -O face_landmarker_v2_with_blendshapes.task -q https://storage.googleapis.com/mediapipe-models/face_landmarker/face_landmarker/float16/1/face_landmarker.task
# !wget -q -O image.png https://storage.googleapis.com/mediapipe-assets/business-person.png

# Imports
import mediapipe as mp
from mediapipe.tasks import python
from mediapipe.tasks.python import vision
from mediapipe import solutions
from mediapipe.framework.formats import landmark_pb2
import numpy as np
import matplotlib.pyplot as plt
import cv2
import pathlib
# from google.colab.patches import cv2_imshow
import csv
import pandas as pd
import tensorflow as tf
import keras_tuner
import math
import time
import os

2024-05-01 16:15:12.525473: I tensorflow/core/util/port.cc:111] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-05-01 16:15:12.551838: E tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:9342] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-05-01 16:15:12.551872: E tensorflow/compiler/xla/stream_executor/cuda/cuda_fft.cc:609] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-05-01 16:15:12.551904: E tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:1518] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-05-01 16:15:12.557983: I tensorflow/core/platform/cpu_feature_g

Using TensorFlow backend


In [2]:
# MediaPipe visualizations


def draw_landmarks_on_image(rgb_image, detection_result):
  face_landmarks_list = detection_result.face_landmarks
  annotated_image = np.copy(rgb_image)

  # Loop through the detected faces to visualize.
  for idx in range(len(face_landmarks_list)):
    face_landmarks = face_landmarks_list[idx]

    # Draw the face landmarks.
    face_landmarks_proto = landmark_pb2.NormalizedLandmarkList()
    face_landmarks_proto.landmark.extend([
      landmark_pb2.NormalizedLandmark(x=landmark.x, y=landmark.y, z=landmark.z) for landmark in face_landmarks
    ])

    solutions.drawing_utils.draw_landmarks(
        image=annotated_image,
        landmark_list=face_landmarks_proto,
        connections=mp.solutions.face_mesh.FACEMESH_TESSELATION,
        landmark_drawing_spec=None,
        connection_drawing_spec=mp.solutions.drawing_styles
        .get_default_face_mesh_tesselation_style())
    solutions.drawing_utils.draw_landmarks(
        image=annotated_image,
        landmark_list=face_landmarks_proto,
        connections=mp.solutions.face_mesh.FACEMESH_CONTOURS,
        landmark_drawing_spec=None,
        connection_drawing_spec=mp.solutions.drawing_styles
        .get_default_face_mesh_contours_style())
    solutions.drawing_utils.draw_landmarks(
        image=annotated_image,
        landmark_list=face_landmarks_proto,
        connections=mp.solutions.face_mesh.FACEMESH_IRISES,
          landmark_drawing_spec=None,
          connection_drawing_spec=mp.solutions.drawing_styles
          .get_default_face_mesh_iris_connections_style())

  return annotated_image

def plot_face_blendshapes_bar_graph(face_blendshapes):
  # Extract the face blendshapes category names and scores.
  face_blendshapes_names = [face_blendshapes_category.category_name for face_blendshapes_category in face_blendshapes]
  face_blendshapes_scores = [face_blendshapes_category.score for face_blendshapes_category in face_blendshapes]
  # The blendshapes are ordered in decreasing score value.
  face_blendshapes_ranks = range(len(face_blendshapes_names))

  fig, ax = plt.subplots(figsize=(12, 12))
  bar = ax.barh(face_blendshapes_ranks, face_blendshapes_scores, label=[str(x) for x in face_blendshapes_ranks])
  ax.set_yticks(face_blendshapes_ranks, face_blendshapes_names)
  ax.invert_yaxis()

  # Label each bar with values
  for score, patch in zip(face_blendshapes_scores, bar.patches):
    plt.text(patch.get_x() + patch.get_width(), patch.get_y(), f"{score:.4f}", va="top")

  ax.set_xlabel('Score')
  ax.set_title("Face Blendshapes")
  plt.tight_layout()
  plt.show()


In [3]:
# a function to write to csv files
def csv_writer(filename, fields, data):

    csvfile = filename
    fields = fields
    with open(csvfile, mode="a") as first:
        csvwriter = csv.writer(first)
        csvwriter.writerow(fields)
        csvwriter.writerows(data)

        return True

In [4]:
# download and upload images
# download
# img = cv2.imread("images.jpg")
# cv2_imshow(img)

#upload
# from google.colab import files
# uploaded = files.upload()

# for filename in uploaded:
#   content = uploaded[filename]
#   with open(filename, 'wb') as f:
#     f.write(content)

# if len(uploaded.keys()):
#   IMAGE_FILE = next(iter(uploaded))
#   print('Uploaded file:', IMAGE_FILE)

In [5]:
#inferencing and visualizing

# STEP 2: Create an FaceLandmarker object.
base_options = python.BaseOptions(model_asset_path='face_landmarker_v2_with_blendshapes.task')
options = vision.FaceLandmarkerOptions(base_options=base_options,
                                       output_face_blendshapes=True,
                                       output_facial_transformation_matrixes=True,
                                       num_faces=1)
detector = vision.FaceLandmarker.create_from_options(options)

# STEP 3: Load the input image.
image = mp.Image.create_from_file("image.png")

# STEP 4: Detect face landmarks from the input image.
detection_result = detector.detect(image)
# print(detection_result.facial_transformation_matrixes)

# STEP 5: Process the detection result. In this case, visualize it.
annotated_image = draw_landmarks_on_image(image.numpy_view(), detection_result)
# img = plt.imshow(annotated_image)
# plt.show()
# cv2_imshow(cv2.cvtColor(annotated_image, cv2.COLOR_RGB2BGR))

libEGL warning: MESA-LOADER: failed to open iris: /usr/lib/dri/iris_dri.so: cannot open shared object file: No such file or directory (search paths /usr/lib/x86_64-linux-gnu/dri:\$${ORIGIN}/dri:/usr/lib/dri, suffix _dri)

libEGL warning: MESA-LOADER: failed to open iris: /usr/lib/dri/iris_dri.so: cannot open shared object file: No such file or directory (search paths /usr/lib/x86_64-linux-gnu/dri:\$${ORIGIN}/dri:/usr/lib/dri, suffix _dri)

libEGL warning: MESA-LOADER: failed to open swrast: /usr/lib/dri/swrast_dri.so: cannot open shared object file: No such file or directory (search paths /usr/lib/x86_64-linux-gnu/dri:\$${ORIGIN}/dri:/usr/lib/dri, suffix _dri)

I0000 00:00:1714572914.255426  367876 task_runner.cc:85] GPU suport is not available: INTERNAL: ; RET_CHECK failure (mediapipe/gpu/gl_context_egl.cc:84) egl_initializedUnable to initialize EGL
W0000 00:00:1714572914.255805  367876 face_landmarker_graph.cc:174] Sets FaceBlendshapesGraph acceleration to xnnpack by default.
libEGL 

In [6]:
# plot bar graphs

# plot_face_blendshapes_bar_graph(detection_result.face_blendshapes[0])
# print(detection_result.face_blendshapes[0])

In [7]:
# loading AffectNet dataset


# data_path = pathlib.Path('/home/samer/Desktop/Big data Small Data/BDSD/Minor_project/AffectNet/AffectNEt/')
# img_data_array=[]
# class_name=[]


# for dir1 in os.listdir(data_path):
#     for file in os.listdir(os.path.join(data_path, dir1)):
#         image_path= os.path.join(data_path, dir1, file)
#         image= cv2.imread(image_path, cv2.COLOR_BGR2RGB)
#         image=cv2.resize(image, (100, 100))
#         image=np.array(image)
#         image = image.astype('float32')
#         if len(image.shape) < 3:
#             continue
#         elif dir1 =="happy":
#             img_data_array.append(image)
#             class_name.append(1)
#         elif dir1 =="sad":
#             img_data_array.append(image)
#             class_name.append(2)
#         elif dir1 =="neutral":
#             img_data_array.append(image)
#             class_name.append(3)

# img_data_array = np.stack(img_data_array, axis=0)
# class_name = np.stack(class_name, axis=0)


In [8]:
# # Processing, cleaning and visualizing the fer2023 dataset
# dataset = []
# Training_set = []
# validation_set = []
# test_set = []
# categories_count = {"0":0, "1":0, "2":0, "3":0, "4":0, "5":0, "6":0}
# skipped = {"0":0, "1":0, "2":0, "3":0, "4":0, "5":0, "6":0}
# z_count = 0
# o_count = 0
# t_count = 0

# with open("blends_validation_set.csv", mode= "r") as data:
#   csvFile = csv.reader(data)
#   for lines in csvFile:
#       if lines[33] == "0" and z_count < 7500:
#         lines[33] = "0"
#         z_count+=1
#         dataset.append(lines)
#       elif lines[33] == "1" and o_count < 7500:
#         lines[33] = '1'
#         o_count +=1
#         dataset.append(lines)
#       elif lines[33] == '2' and t_count < 7500:
#         lines[33] = '2'
#         t_count+=1
#         dataset.append(lines) 
        
#   print(dataset[1:6])
#   # iterate over the training dataset
#   for i in range(len(dataset)):
#     if categories_count[str(dataset[i][33])] == 7500:
#       continue
#     else:
      # print(categories_count[dataset[i][0]])
      # categories_count[str(dataset[i][33])] = categories_count[str(dataset[i][33])] + 1
    # image = np.array(Training_set[i][1].split(' ')).reshape(48, 48, 1).astype(np.uint8)
    # image = cv2.cvtColor(image, cv2.COLOR_GRAY2RGB)
    # print(image.shape)
    # rgb_frame = mp.Image(image_format=mp.ImageFormat.SRGB,data=image)
    # detection_result = detector.detect(rgb_frame)
    # print("emotion = ", Training_set[i][0])
    # img = plt.imshow(image)
    # plt.show()
    # # Skip and delete the image if not understood by mediapipe
    # if detection_result.face_blendshapes == []:
    #   skipped[Training_set[i][0]] = skipped[Training_set[i][0]] + 1
    # else:
    #   img = plt.imshow(image)
    #   plt.show()
    #   continue

  # print("This is categories count", categories_count)
  # print("This is skipped", skipped)


# plot_face_blendshapes_bar_graph(detection_result.face_blendshapes[0])
# annotated_image = draw_landmarks_on_image(rgb_frame.numpy_view(), detection_result)
# cv2_imshow(cv2.cvtColor(annotated_image, cv2.COLOR_RGB2BGR))



In [9]:
# cleaning the dataset

# training_set = []
# validation_set = []
# test_set = []

# for i in dataset:
#     if i[2] == 'Training':
#         training_set.append(i)
#     elif i[2] == 'PublicTest':
#         validation_set.append(i)
#     elif i[2] == 'PrivateTest':
#         test_set.append(i)

# training_set_hns = []
# validation_set_hns = []
# test_set_hns = []

# for lines in training_set:
#       image = np.array(lines[1].split(' ')).reshape(48, 48, 1).astype(np.uint8)
#       image = cv2.cvtColor(image, cv2.COLOR_GRAY2RGB)
#     #   plt.imshow(image)
#     #   plt.show()
#       frame = mp.Image(image_format=mp.ImageFormat.SRGB,data=image)
#       detection_result = detector.detect(frame)
#       if detection_result.face_blendshapes == []:
#         continue
#       else:
#         training_set_hns.append(lines)

# for liness in validation_set:
#       imagee = np.array(liness[1].split(' ')).reshape(48, 48, 1).astype(np.uint8)
#       imagee = cv2.cvtColor(imagee, cv2.COLOR_GRAY2RGB)
#     #   plt.imshow(image)
#     #   plt.show()
#       framee = mp.Image(image_format=mp.ImageFormat.SRGB,data=imagee)
#       detection_result = detector.detect(framee)
#       if detection_result.face_blendshapes == []:
#         continue
#       else:
#         validation_set_hns.append(liness)

# for linesss in test_set:
#       imageee = np.array(linesss[1].split(' ')).reshape(48, 48, 1).astype(np.uint8)
#       imageee = cv2.cvtColor(imageee, cv2.COLOR_GRAY2RGB)
#     #   plt.imshow(image)
#     #   plt.show()
#       frameee = mp.Image(image_format=mp.ImageFormat.SRGB,data=imageee)
#       detection_result = detector.detect(frameee)
#       if detection_result.face_blendshapes == []:
#         continue
#       else:
#         test_set_hns.append(linesss)

# fields = ["emotion", "pixels", "Usage"]
# csv_writer("training_set_hns.csv", fields, training_set_hns)
# csv_writer("validation_set_hns.csv", fields, validation_set_hns)
# csv_writer("test_set_hns.csv", fields, test_set_hns)


In [10]:
# Augmenting images


# augmented_training_set = []
# training_images = []
# training_labels = []
# print(len(Training_set))

# for i in range(math.floor(len(training_set_hns))):
#     image = np.array(training_set_hns[i][1].split(' ')).reshape(48, 48, 1).astype(np.uint8)
#     image = cv2.cvtColor(image, cv2.COLOR_GRAY2RGB)
#     training_images.append(image)
#     training_labels.append(int(training_set_hns[i][0]))


# # rescaling and augmenting images models
# rescaling1 = tf.keras.Sequential([
#   tf.keras.layers.Rescaling(1./255)
# ])

# rescaling2 = tf.keras.Sequential([
#   tf.keras.layers.Rescaling(1.*255)
# ])

# augment = tf.keras.Sequential([
#   tf.keras.layers.RandomFlip("horizontal"),
#   tf.keras.layers.RandomRotation(0.1)
# ])

# for ele in range(len(training_images)):
# scale down the image and augment
#   img = training_images[ele]
#   label = training_labels[ele]
#   image = rescaling1(img)
#   aug_image = augment(image)
# #   scale up the image cast to an integer and transform into a numpy array
#   aug_image = rescaling2(aug_image)
#   aug_image = tf.cast(aug_image, tf.uint8)
#   aug_image = np.array(aug_image)
#   flatten_image = aug_image.flatten()
#   flat_aug_image = [flatten_image[i] for i in range(0,len(flatten_image),3)]
#   # flattt = np.reshape(flat_aug_image,(48,48))
#   # plt.imshow(flattt)
#   # plt.show()
#   frame = mp.Image(image_format=mp.ImageFormat.SRGB,data=aug_image)
#   detection_result = detector.detect(frame)
#   if detection_result.face_blendshapes == []:
#     continue
#   else:
#     element = [training_labels[ele]]
#     for i in flat_aug_image:
#       element.append(i)
#     augmented_training_set.append([element[0],str(element[1:]).replace(',',"").replace('[','').replace(']',''),'Training'])

# csv_writer("training_set_hns.csv", ['emotion','pixels'], augmented_training_set)

# print(detection_result.face_blendshapes[0])
# annotated_image = draw_landmarks_on_image(frame.numpy_view(), detection_result)
# plt.imshow(annotated_image)
# plt.show()



In [11]:
# choosing relevant blendshapes
# blendS_to_print = ['1', '2', '3', '4', '5', '9', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '20', '25', '30', '31', '34', '35', '36', '37', '38', '40', '42', '44', '45', '46', '47', '48', '49', 'emotion']

# blend_shapes = dict()
# for i in range(0,52):
#     blend_shapes[str(i)] = 0

# print(blend_shapes)
# sad = 0
# happy = 0
# counter = 0

#   # find which blendshapes are most relevant to happiness and sadness
# for i in range(len(training_set_hns)):
#     image = np.array(training_set_hns[i][1].split(' ')).reshape(48, 48, 1).astype(np.uint8)
#     image = cv2.cvtColor(image, cv2.COLOR_GRAY2RGB)
#     frame = mp.Image(image_format=mp.ImageFormat.SRGB,data=image)
#     detection_result = detector.detect(frame)
#     if detection_result.face_blendshapes == []:
#         continue
#     else:
#         counter += 1
#     if counter %500 == 0:
#         time.sleep(5)
#     for i in detection_result.face_blendshapes[0]:
#         if i.score > 0.4:
#             blend_shapes[str(i.index)] = blend_shapes[str(i.index)] + 1
# print(blend_shapes)

# detect annotate and plot blendshapes for the image
# frame = mp.Image(image_format=mp.ImageFormat.SRGB,data=aug_image)
# detection_result = detector.detect(frame)
# annotated_image = draw_landmarks_on_image(frame.numpy_view(), detection_result)
# cv2_imshow(cv2.cvtColor(annotated_image, cv2.COLOR_RGB2BGR))
# plot_face_blendshapes_bar_graph(detection_result.face_blendshapes[0])

In [12]:
# if-else classification

# if detection_result.face_blendshapes[0][44].score > 0.5 and detection_result.face_blendshapes[0][45].score > 0.5 :
#   print("Happy")
# elif detection_result.face_blendshapes[0][42].score > 0.5:
#   print("Sad")


In [13]:
# creating blendshapes dataset

# val_set = []
# val_images = []
# val_labels = []

# blendS_to_print = ['1', '2', '3', '4', '5', '9', '10', '11', '12', '13', '14', '15', '16', '17', '18', '19', '20', '25', '30', '31', '34', '35', '36', '37', '38', '40', '42', '44', '45', '46', '47', '48', '49','999']
# with open("validation_set_hns.csv", mode= "r") as data:
#   csvFile = csv.reader(data)
#   next(csvFile)
#   for lines in csvFile:
#     val_set.append(lines)
# #   print(test_set[0])
#   for i in range(len(val_set)):
#     # print(training_set[i][1])
#     image = np.array(val_set[i][1].split(' ')).reshape(48, 48, 1).astype(np.uint8)
#     image = cv2.cvtColor(image, cv2.COLOR_GRAY2RGB)
#     val_images.append(image)
#     val_labels.append(int(val_set[i][0]))

# arr = np.zeros((len(val_images), 34))

# print(len(val_images))
# arr[0,:]= blendS_to_print
# for ele in range(len(val_images)-1):
#   img = val_images[ele]
#   label = val_labels[ele]
#   frame = mp.Image(image_format=mp.ImageFormat.SRGB,data=img)
#   detection_result = detector.detect(frame)
# #   print(detection_result.face_blendshapes[0])
#   for category in detection_result.face_blendshapes[0]:
#     if str(category.index) in blendS_to_print:
#        arr[ele, blendS_to_print.index(f"{category.index}")] = category.score
#        arr[ele, 33] = label
#     else:
#        continue
    # print(arr)

# np.savetxt("blends_validation_set.csv", arr, delimiter = ",")

In [14]:
# load data for LSTM model

traindata = []
blend_set = []
labels_set = []
with open("blends_train_set.csv", mode= "r") as data:
  csvFile = csv.reader(data)
  next(csvFile)
  for line in csvFile:
    traindata.append(line[:])
  np.random.shuffle(traindata)
  for lines in traindata:
      blend_set.append(lines[0:33])
      labels_set.append(lines[33])
blends_set = np.array(blend_set, dtype=np.float64)
labels_set = np.array(labels_set, dtype=np.float64)
#Reshaping Array
X_train = np.reshape(blends_set, (22500, 33,1))
Y_train = np.reshape(labels_set, (22500,1)).astype('int')
Y_train = tf.keras.utils.to_categorical(Y_train, num_classes=3)

# load validation data
valdata = []
val_blend_set = []
val_labels_set = []
with open("blends_validation_set.csv", mode= "r") as val_data:
  csvFile = csv.reader(val_data)
  next(csvFile)
  for line in csvFile:
    valdata.append(line[:])
  np.random.shuffle(valdata)
  for lines in valdata:
      val_blend_set.append(lines[0:33])
      val_labels_set.append(lines[33])
val_blend_set = np.array(val_blend_set, dtype=np.float64)
val_labels_set = np.array(val_labels_set, dtype=np.float64)
X_val = np.reshape(val_blend_set, (1947, 33,1))
y_val = np.reshape(val_labels_set, (1947,1)).astype('int')
y_val = tf.keras.utils.to_categorical(y_val, num_classes=3)

# normalize data
# norm = tf.keras.layers.Normalization()
# norm.adapt(X_train)
# X_train = norm(X_train)
# X_train = np.array(X_train)

# norm.adapt(X_val)
# X_val = norm(X_val)
# X_val = np.array(X_val)

In [15]:
# keras tuner for LSTM model


# def build_model(hp):
  
#   learning_rate = hp.Float("lr", min_value=1e-5, max_value=1e-4, sampling="log")

# # model structure
#   model = tf.keras.Sequential([
#       tf.keras.layers.LSTM(units = 498, activation = 'selu', recurrent_activation='sigmoid', return_sequences= True,recurrent_dropout=0.2, dropout=0.2,kernel_initializer='glorot_uniform',
#                           use_bias=True, kernel_regularizer=tf.keras.regularizers.L2(l2=0.001), go_backwards=True),
#       tf.keras.layers.LSTM(units = 330, activation = 'selu', recurrent_activation='sigmoid', return_sequences= True,recurrent_dropout=0.2, dropout=0.2,kernel_initializer='glorot_uniform',
#                           use_bias=True, kernel_regularizer=tf.keras.regularizers.L2(l2=0.001), go_backwards=True),
#       tf.keras.layers.LSTM(units = 224, activation = 'selu', recurrent_activation='sigmoid', return_sequences= True,recurrent_dropout=0.2, dropout=0.2,kernel_initializer='glorot_uniform',
#                           use_bias=True, kernel_regularizer=tf.keras.regularizers.L2(l2=0.001), go_backwards=True),
#       tf.keras.layers.LSTM(units = 128, activation = 'selu', recurrent_activation='sigmoid', return_sequences= True,recurrent_dropout=0.2, dropout=0.2,kernel_initializer='glorot_uniform',
#                           use_bias=True, kernel_regularizer=tf.keras.regularizers.L2(l2=0.001), go_backwards=True),
#       tf.keras.layers.LSTM(units = 64, activation = 'selu', recurrent_activation='sigmoid', return_sequences= True, recurrent_dropout=0.2, dropout=0.2,kernel_initializer='glorot_uniform',
#                           use_bias=True, kernel_regularizer=tf.keras.regularizers.L2(l2=0.001), go_backwards=True),
#       tf.keras.layers.LSTM(units = 16, activation = 'selu', recurrent_activation='sigmoid', return_sequences= False, recurrent_dropout=0.2, use_bias=True, 
#                           kernel_regularizer=tf.keras.regularizers.L2(l2=0.001), go_backwards=True),
#       tf.keras.layers.Dense(units = 3, activation = 'softmax'),
#   ])


  # model = tf.keras.Sequential([ 
  #     tf.keras.layers.Dense(units = 330, activation = 'relu', batch_input_shape = (64,33)),    
  #     tf.keras.layers.Dense(units = 300, activation = 'relu', kernel_regularizer='l2'),
  #     tf.keras.layers.Dropout(0.2),                         
  #     tf.keras.layers.Dense(units = 250, activation = 'relu', kernel_regularizer='l2'),                         
  #     tf.keras.layers.Dropout(0.2),                               
  #     tf.keras.layers.Dense(units = 220, activation = 'relu', kernel_regularizer='l2'),   
  #     tf.keras.layers.Dropout(0.2),                                                
  #     tf.keras.layers.Dense(units = 200, activation = 'relu', kernel_regularizer='l2'), 
  #     tf.keras.layers.Dropout(0.2),                                                       
  #     tf.keras.layers.Dense(units = 150, activation = 'relu', kernel_regularizer='l2'), 
  #     tf.keras.layers.Dropout(0.2),                                                       
  #     tf.keras.layers.Dense(units = 10, activation = 'relu', kernel_regularizer='l2'),                         
  #     tf.keras.layers.Dense(units = 3, activation = 'softmax'),
  # ])




# Compiling the RNN
#   model.compile(loss=tf.keras.losses.CategoricalCrossentropy(),
#               optimizer= tf.keras.optimizers.Adam(learning_rate = 3.2e-05, global_clipnorm=1, use_ema=True, ema_momentum=0.99, amsgrad = True, beta_1=0.9, beta_2=0.999),
#               metrics = [tf.keras.metrics.CategoricalAccuracy(), tf.keras.metrics.F1Score()])

#   return model 

# build_model(keras_tuner.HyperParameters())

# tuner = keras_tuner.RandomSearch(
#     hypermodel=build_model,
#     max_trials=15,
#     objective=keras_tuner.Objective('val_categorical_accuracy', 'max'),
#     executions_per_trial=1,
#     overwrite=True,
#     directory="/home/samer/Desktop/Big data Small Data/BDSD/Minor_project/emotion_estimation/",
#     project_name="Emotion_estimation_tuning",
# )

# tuner.search_space_summary()

# tuner.search(x=X_train, y=Y_train, validation_data = (X_val,y_val), epochs=600, batch_size = 64)

# tuner.results_summary()



# EStop = tf.keras.callbacks.EarlyStopping(monitor='val_loss',patience=5,restore_best_weights=True)


In [16]:
# LSTM model fitting

# model = tf.keras.Sequential([
#     tf.keras.layers.LSTM(units = 33, activation = 'relu', return_sequences= True),
#     tf.keras.layers.LSTM(units = 12, activation = 'relu', return_sequences= False),
#     tf.keras.layers.Dense(units = 3, activation = 'softmax'),
# ])


# model = tf.keras.Sequential([ 
#     tf.keras.layers.Dense(units = 330, activation = 'relu', batch_input_shape = (64,33)),    
#     tf.keras.layers.Dense(units = 300, activation = 'relu', kernel_regularizer='l2'),
#     tf.keras.layers.Dropout(0.2),                         
#     tf.keras.layers.Dense(units = 250, activation = 'relu', kernel_regularizer='l2'),                         
#     tf.keras.layers.Dropout(0.2),                               
#     tf.keras.layers.Dense(units = 220, activation = 'relu', kernel_regularizer='l2'),   
#     tf.keras.layers.Dropout(0.2),                                                
#     tf.keras.layers.Dense(units = 200, activation = 'relu', kernel_regularizer='l2'), 
#     tf.keras.layers.Dropout(0.2),                                                       
#     tf.keras.layers.Dense(units = 150, activation = 'relu', kernel_regularizer='l2'), 
#     tf.keras.layers.Dropout(0.2),                                                       
#     tf.keras.layers.Dense(units = 10, activation = 'relu', kernel_regularizer='l2'),                         
#     tf.keras.layers.Dense(units = 3, activation = 'softmax'),
# ])


model = tf.keras.Sequential([
    tf.keras.layers.LSTM(units = 498, activation = 'selu', recurrent_activation='sigmoid', return_sequences= True,recurrent_dropout=0.2, dropout=0.2,kernel_initializer='glorot_uniform',
                        use_bias=True, kernel_regularizer=tf.keras.regularizers.L2(l2=0.001), go_backwards=True),
    tf.keras.layers.LSTM(units = 330, activation = 'selu', recurrent_activation='sigmoid', return_sequences= True,recurrent_dropout=0.2, dropout=0.2,kernel_initializer='glorot_uniform',
                        use_bias=True, kernel_regularizer=tf.keras.regularizers.L2(l2=0.001), go_backwards=True),
    tf.keras.layers.LSTM(units = 224, activation = 'selu', recurrent_activation='sigmoid', return_sequences= True,recurrent_dropout=0.2, dropout=0.2,kernel_initializer='glorot_uniform',
                        use_bias=True, kernel_regularizer=tf.keras.regularizers.L2(l2=0.001), go_backwards=True),
    tf.keras.layers.LSTM(units = 128, activation = 'selu', recurrent_activation='sigmoid', return_sequences= True,recurrent_dropout=0.2, dropout=0.2,kernel_initializer='glorot_uniform',
                        use_bias=True, kernel_regularizer=tf.keras.regularizers.L2(l2=0.001), go_backwards=True),
    tf.keras.layers.LSTM(units = 64, activation = 'selu', recurrent_activation='sigmoid', return_sequences= True, recurrent_dropout=0.2, dropout=0.2,kernel_initializer='glorot_uniform',
                        use_bias=True, kernel_regularizer=tf.keras.regularizers.L2(l2=0.001), go_backwards=True),
    tf.keras.layers.LSTM(units = 16, activation = 'selu', recurrent_activation='sigmoid', return_sequences= False, recurrent_dropout=0.2, use_bias=True, 
                        kernel_regularizer=tf.keras.regularizers.L2(l2=0.001), go_backwards=True),
    tf.keras.layers.Dense(units = 3, activation = 'softmax'),
])

# Compiling the RNN
# model.compile(loss=tf.keras.losses.CategoricalCrossentropy(),
#             optimizer= tf.keras.optimizers.Adam(learning_rate = 0.00464489028556945,),# clipnorm=1),
#             metrics = [tf.keras.metrics.CategoricalAccuracy(), tf.keras.metrics.F1Score()])

# best learning rate so far with 600 epochs Adam(learning_rate = 3.206e-05, global_clipnorm=1, use_ema=True, ema_momentum=0.99, amsgrad = True, beta_1=0.9, beta_2=0.999)

model.compile(loss=tf.keras.losses.CategoricalCrossentropy(),
            optimizer= tf.keras.optimizers.AdamW(learning_rate = 3.206e-05, global_clipnorm=1, use_ema=True, ema_momentum=0.99, amsgrad = True),
            metrics = [tf.keras.metrics.CategoricalAccuracy(), tf.keras.metrics.F1Score()])


# Fitting the RNN to the Training set
model.fit(x=X_train, y=Y_train, validation_data = (X_val,y_val) ,epochs = 1000, batch_size=64)

Epoch 1/1000


2024-05-01 16:15:18.551702: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:894] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-05-01 16:15:18.600641: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:894] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysfs-bus-pci#L344-L355
2024-05-01 16:15:18.600823: I tensorflow/compiler/xla/stream_executor/cuda/cuda_gpu_executor.cc:894] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero. See more at https://github.com/torvalds/linux/blob/v6.0/Documentation/ABI/testing/sysf

352/352 [==============================] - 112s 288ms/step - loss: 2.3752 - categorical_accuracy: 0.5965 - f1_score: 0.5949 - val_loss: 2.1120 - val_categorical_accuracy: 0.6810 - val_f1_score: 0.6358
Epoch 2/1000
352/352 [==============================] - 107s 305ms/step - loss: 2.0392 - categorical_accuracy: 0.6180 - f1_score: 0.6150 - val_loss: 1.8851 - val_categorical_accuracy: 0.6605 - val_f1_score: 0.6292
Epoch 3/1000
352/352 [==============================] - 108s 306ms/step - loss: 1.8224 - categorical_accuracy: 0.6154 - f1_score: 0.6136 - val_loss: 1.6899 - val_categorical_accuracy: 0.6394 - val_f1_score: 0.5820
Epoch 4/1000
352/352 [==============================] - 107s 304ms/step - loss: 1.6499 - categorical_accuracy: 0.6184 - f1_score: 0.6157 - val_loss: 1.5193 - val_categorical_accuracy: 0.6764 - val_f1_score: 0.6333
Epoch 5/1000
352/352 [==============================] - 106s 300ms/step - loss: 1.5178 - categorical_accuracy: 0.6249 - f1_score: 0.6229 - val_loss: 1.4179 -

In [40]:
# evaluate

test_blend_set = []
test_labels_set = []
with open("blends_test_set.csv", mode= "r") as test_data:
  csvFile = csv.reader(test_data)
  next(csvFile)
  for lines in csvFile:
      test_blend_set.append(lines[0:33])
      test_labels_set.append(lines[33])
test_blend_set = np.array(test_blend_set, dtype=np.float64)
test_labels_set = np.array(test_labels_set, dtype=np.float64).astype('int')
test_labels_set = tf.keras.utils.to_categorical(test_labels_set, num_classes=3)
X_test = np.reshape(test_blend_set, (1914, 33,1))

model.evaluate(X_test,test_labels_set)


# model.save('LSTM_model_73%_test_acc')

60/60 [==============================] - 0s 2ms/step - loss: 0.6819 - categorical_accuracy: 0.6620 - f1_score: 0.6192


[0.6819400191307068,
 0.661964476108551,
 array([0.88651216, 0.5176252 , 0.45360824], dtype=float32)]

In [55]:
# predict test classes
new_model = tf.keras.models.load_model('LSTM_model_73%_test_acc')
predictions = []
for inst in X_test:
    inst = np.array(inst, dtype=np.float64)
    inst = np.reshape(inst, (1,33,1))
    print(inst)
    y_pred = new_model.predict(inst, verbose=0)
    y_pred = np.argmax(y_pred)
    predictions.append(y_pred)
    print(predictions)

[[[2.93779001e-02]
  [1.35308430e-02]
  [1.70884083e-03]
  [1.41521245e-01]
  [3.74834418e-01]
  [5.31980038e-01]
  [2.17520356e-01]
  [2.74305761e-01]
  [2.41327673e-01]
  [1.21861519e-02]
  [3.89096051e-01]
  [3.84085327e-01]
  [7.34120701e-03]
  [3.08200493e-02]
  [4.68784049e-02]
  [4.76026267e-01]
  [5.90697050e-01]
  [8.01335089e-03]
  [7.19946329e-05]
  [1.29380031e-04]
  [1.30426395e-03]
  [3.73510434e-03]
  [2.76368689e-02]
  [6.62825210e-03]
  [6.82605624e-01]
  [8.60310569e-02]
  [1.60373542e-02]
  [1.05542840e-05]
  [4.35985976e-06]
  [6.27090049e-05]
  [9.95753566e-04]
  [2.49157110e-05]
  [8.11117661e-06]]]
[1]
[[[2.31572405e-01]
  [1.98854759e-01]
  [2.40493868e-03]
  [3.09329219e-02]
  [1.94969662e-02]
  [3.59698106e-03]
  [2.04973179e-03]
  [1.43845472e-02]
  [1.45962061e-02]
  [1.59118593e-01]
  [1.31086297e-02]
  [1.58460308e-02]
  [1.65924564e-01]
  [3.06573540e-01]
  [3.43823314e-01]
  [1.13825709e-01]
  [2.74558589e-02]
  [1.45620480e-01]
  [5.88442711e-03]
  [6.2

In [56]:
# confusion matrix
ground_truth = []
for i in test_labels_set:
    i = np.argmax(i)
    ground_truth.append(i)
tf.math.confusion_matrix(ground_truth,predictions,num_classes=3,dtype=tf.dtypes.int32,)

<tf.Tensor: shape=(3, 3), dtype=int32, numpy=
array([[754,  22,  57],
       [ 58, 209, 228],
       [ 54,  91, 441]], dtype=int32)>